In [1]:
# NumPy compatibility patch FIRST - before importing mlens
import numpy as np

# Fix deprecated np.int for NumPy 1.20+ (mlens library still uses deprecated aliases)
if not hasattr(np, 'int'):
    np.int = np.int64
    np.float = np.float64
    np.complex = np.complex128
    np.object = np.object_
    np.str = np.str_
    np.long = np.int64
    np.unicode = np.str_

# example of a super learner using the mlens library
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score
from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import RandomForestClassifier, GradientBoostingClassifier
from xgboost import XGBClassifier
import lightgbm as lgb
from catboost import CatBoostClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.svm import SVC
from sklearn.neighbors import KNeighborsClassifier
from mlens.ensemble import SuperLearner

import sys
sys.path.append('./utils')  # make sure Python knows where to look

# Display full output in Jupyter
import pandas as pd
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
pd.set_option('display.width', None)
pd.set_option('display.max_colwidth', None)

import time
import datetime
import sklearn
from imblearn import under_sampling, over_sampling, ensemble
import lightgbm as lgb
from catboost import CatBoostClassifier 
from xgboost import XGBClassifier
from sklearn.ensemble import GradientBoostingClassifier

import transform_data_functions as utils_transform_data
import plot_data_functions as utils_plot_data
import ml_training_functions as utils_training
import import_shared_functions as utils_import
import file_handler_functions as utils_file
import performance_assessment_function as utils_assessment


[MLENS] backend: threading


In [2]:
# Load data from the 2018-07-25 to the 2018-08-14
DIR_INPUT='./data/simulated-data-transformed/' 

BEGIN_DATE = "2018-06-11"
END_DATE = "2018-08-14"

print("Load  files")
%time transactions_df = utils_file.read_from_files(DIR_INPUT, BEGIN_DATE, END_DATE)
print("{0} transactions loaded, containing {1} fraudulent transactions".format(len(transactions_df),transactions_df.TX_FRAUD.sum()))

START_DATE = "2018-07-25"
delta_train = delta_delay = delta_test = delta_valid = delta_assessment = 7

# Number of folds for the prequential validation
n_folds = 4

start_date_training = datetime.datetime.strptime(START_DATE, "%Y-%m-%d")
start_date_test = start_date_training+datetime.timedelta(days=delta_train+delta_delay)

start_date_training_for_valid = start_date_training+datetime.timedelta(days=-(delta_delay+delta_valid))
start_date_training_for_test = start_date_training+datetime.timedelta(days=(n_folds-1)*delta_test)

Load  files
CPU times: user 113 ms, sys: 145 ms, total: 258 ms
Wall time: 352 ms
622892 transactions loaded, containing 5515 fraudulent transactions
CPU times: user 113 ms, sys: 145 ms, total: 258 ms
Wall time: 352 ms
622892 transactions loaded, containing 5515 fraudulent transactions


In [3]:
# Specified input features for model training and target features for predictions

output_feature = "TX_FRAUD"

input_features = ['TX_AMOUNT','TX_DURING_WEEKEND', 'TX_DURING_NIGHT', 'CUSTOMER_ID_NB_TX_1DAY_WINDOW',
       'CUSTOMER_ID_AVG_AMOUNT_1DAY_WINDOW', 'CUSTOMER_ID_NB_TX_7DAY_WINDOW',
       'CUSTOMER_ID_AVG_AMOUNT_7DAY_WINDOW', 'CUSTOMER_ID_NB_TX_30DAY_WINDOW',
       'CUSTOMER_ID_AVG_AMOUNT_30DAY_WINDOW', 'TERMINAL_ID_NB_TX_1DAY_WINDOW',
       'TERMINAL_ID_RISK_1DAY_WINDOW', 'TERMINAL_ID_NB_TX_7DAY_WINDOW',
       'TERMINAL_ID_RISK_7DAY_WINDOW', 'TERMINAL_ID_NB_TX_30DAY_WINDOW',
       'TERMINAL_ID_RISK_30DAY_WINDOW']


# Only keep columns that are needed as argument to the custom scoring function
# (in order to reduce the serialization time of transaction dataset)
transactions_df_scorer = transactions_df[['CUSTOMER_ID', 'TX_FRAUD','TX_TIME_DAYS']]

# card_precision_top_100 = sklearn.metrics.make_scorer(utils_import.card_precision_top_k_custom, 
#                                                      needs_proba=True, 
#                                                      top_k=100, 
#                                                      transactions_df=transactions_df_scorer)

def card_precision_scorer(estimator, X, y):
    # estimator must support predict_proba
    probs = estimator.predict_proba(X)[:, 1]
    # use the transactions metadata indexed by the current CV test fold rows
    preds_df = transactions_df_scorer.loc[X.index].copy()
    preds_df['predictions'] = probs
    # utils_training.card_precision_top_k returns (nb_list, list_per_day, mean)
    _, _, mean_cp = utils_training.card_precision_top_k(preds_df, 100)
    return mean_cp

performance_metrics_list_grid = ['roc_auc', 'average_precision', 'card_precision@100']
performance_metrics_list = ['AUC ROC', 'Average precision', 'Card Precision@100']

scoring = {'roc_auc':'roc_auc',
           'average_precision': 'average_precision',
           'card_precision@100': card_precision_scorer,
           }

In [4]:
best_params = utils_file.load_model_data('best_params_ensembles.pkl')[0]
best_params

Object successfully loaded from pickle file:


{'BalancedBaggingClassifier': {'bootstrap': True,
  'estimator': DecisionTreeClassifier(max_depth=20, random_state=0),
  'n_estimators': 100,
  'n_jobs': -1,
  'random_state': 0,
  'sampler': RandomUnderSampler(),
  'sampling_strategy': 0.1},
 'BalancedRandomForestClassifier': {'max_depth': 50,
  'n_estimators': 100,
  'n_jobs': -1,
  'random_state': 0,
  'sampling_strategy': 0.1},
 'CatBoostClassifier': {'depth': 4,
  'iterations': 500,
  'learning_rate': 0.05,
  'random_state': 0,
  'scale_pos_weight': 1},
 'GradientBoostingClassifier': {'learning_rate': 0.05,
  'max_depth': 5,
  'n_estimators': 100,
  'random_state': 0},
 'XGBClassifier': {'learning_rate': 0.1,
  'max_depth': 3,
  'n_estimators': 50,
  'n_jobs': -1,
  'random_state': 0,
  'scale_pos_weight': 10},
 'LGBMClassifier': {'learning_rate': 0.1,
  'max_depth': 3,
  'n_estimators': 50,
  'n_jobs': -1,
  'random_state': 0,
  'scale_pos_weight': 1},
 'LogisticRegression': {'C': 0.1, 'random_state': 0}}

In [5]:
model_list = {
    'LogisticRegression': LogisticRegression(),
    'BalancedBaggingClassifier': ensemble.BalancedBaggingClassifier(),
    'BalancedRandomForestClassifier': ensemble.BalancedRandomForestClassifier(),
    'GradientBoostingClassifier': GradientBoostingClassifier(),
    'LGBMClassifier': lgb.LGBMClassifier(),
    'XGBClassifier': XGBClassifier(),
    'CatBoostClassifier': CatBoostClassifier(),
}

In [6]:
# create a list of base-models
def get_models():
    temp_models = list()
    for name, best_param in best_params.items():
        model = model_list[name]
        for k, v in best_param.items():
            setattr(model, k, v)
        print(model)
        temp_models.append(model)
    return temp_models

In [7]:
# create the super learner
def get_super_learner(train_df, scorer, cv):
	ensemble = SuperLearner(scorer=scorer, folds=cv, sample_size=len(train_df), random_state=0, raise_on_exception=True)
	# add base models
	models = get_models()
	ensemble.add(models)
	# add the meta model
	ensemble.add_meta(LogisticRegression(solver='lbfgs', random_state=0))
	return ensemble

In [8]:
train_df, test_df = utils_transform_data.get_train_test_set(transactions_df, start_date_training, delta_train, delta_delay ,delta_test)

In [16]:
# Split dataset for Cross validation
prequential_split_indices=utils_training.prequentialSplit(transactions_df,
                                               start_date_training=start_date_training, 
                                               n_folds=n_folds, 
                                               delta_train=delta_train, 
                                               delta_delay=delta_delay, 
                                               delta_assessment=delta_assessment)

In [ ]:
ensemble = get_super_learner(train_df, scorer=scoring, cv=4)
sampler_list = [('sampler1', over_sampling.SMOTE()),
                ('sampler2', under_sampling.RandomUnderSampler())]
parameters = {'sampler1__sampling_strategy':[0.1], 
              'sampler2__sampling_strategy':[0.1, 0.5, 1], 
              'sampler1__random_state':[0], 'sampler2__random_state':[0]}

start_time = time.time()

logreg_performance_hybrid = utils_training.model_selection_wrapper_with_sample(
                                        transactions_df=transactions_df,
                                        classifier=ensemble,
                                        sampler_list=sampler_list,
                                        input_features=input_features,
                                        output_feature=output_feature,
                                        parameters=parameters,
                                        scoring=scoring,
                                        cv=prequential_split_indices,
                                        start_date_training_for_valid=start_date_training_for_valid,
                                        start_date_training_for_test=start_date_training_for_test,
                                        n_folds=n_folds,
                                        delta_train=delta_train, 
                                        delta_delay=delta_delay, 
                                        delta_assessment=delta_assessment,
                                        performance_metrics_list_grid=performance_metrics_list_grid,
                                        performance_metrics_list=performance_metrics_list,
                                        type_search="random",
                                        n_jobs=-1)

execution_time_weighted_logreg_hybrid = time.time()-start_time

BalancedBaggingClassifier(estimator=DecisionTreeClassifier(max_depth=20,
                                                           random_state=0),
                          n_estimators=100, n_jobs=-1, random_state=0,
                          sampler=RandomUnderSampler(), sampling_strategy=0.1)
BalancedRandomForestClassifier(max_depth=50, n_jobs=-1, random_state=0,
                               sampling_strategy=0.1)
GradientBoostingClassifier(learning_rate=0.05, max_depth=5, random_state=0)
XGBClassifier(base_score=None, booster=None, callbacks=None,
              colsample_bylevel=None, colsample_bynode=None,
              colsample_bytree=None, device=None, early_stopping_rounds=None,
              enable_categorical=False, eval_metric=None, feature_types=None,
              feature_weights=None, gamma=None, grow_policy=None,
              importance_type=None, interaction_constraints=None,
              learning_rate=0.1, max_bin=None, max_cat_threshold=None,
              max_

python(6429) MallocStackLogging: can't turn off malloc stack logging because it was not enabled.
python(6430) MallocStackLogging: can't turn off malloc stack logging because it was not enabled.
python(6431) MallocStackLogging: can't turn off malloc stack logging because it was not enabled.
python(6432) MallocStackLogging: can't turn off malloc stack logging because it was not enabled.
python(6430) MallocStackLogging: can't turn off malloc stack logging because it was not enabled.
python(6431) MallocStackLogging: can't turn off malloc stack logging because it was not enabled.
python(6432) MallocStackLogging: can't turn off malloc stack logging because it was not enabled.
python(6433) MallocStackLogging: can't turn off malloc stack logging because it was not enabled.
python(6434) MallocStackLogging: can't turn off malloc stack logging because it was not enabled.
python(6433) MallocStackLogging: can't turn off malloc stack logging because it was not enabled.
python(6434) MallocStackLoggin

Learning rate set to 0.036931
Learning rate set to 0.036948
Learning rate set to 0.036948
Learning rate set to 0.037017
0:	learn: 0.6461839	total: 1.14s	remaining: 18m 54s
Learning rate set to 0.037017
0:	learn: 0.6461839	total: 1.14s	remaining: 18m 54s
0:	learn: 0.6459457	total: 745ms	remaining: 12m 23s
Learning rate set to 0.036934
0:	learn: 0.6459457	total: 745ms	remaining: 12m 23s
Learning rate set to 0.036934
1:	learn: 0.6055700	total: 1.65s	remaining: 13m 43s
0:	learn: 0.6515374	total: 313ms	remaining: 5m 12s
1:	learn: 0.6071313	total: 1.39s	remaining: 11m 32s
1:	learn: 0.6055700	total: 1.65s	remaining: 13m 43s
0:	learn: 0.6515374	total: 313ms	remaining: 5m 12s
1:	learn: 0.6071313	total: 1.39s	remaining: 11m 32s
2:	learn: 0.5758790	total: 1.44s	remaining: 7m 58s
0:	learn: 0.6439230	total: 896ms	remaining: 14m 55s
3:	learn: 0.5456696	total: 1.54s	remaining: 6m 22s
4:	learn: 0.5161607	total: 1.55s	remaining: 5m 7s
2:	learn: 0.5678644	total: 2.01s	remaining: 11m 8s
2:	learn: 0.57587

ValueError: 
All the 12 fits failed.
It is very likely that your model is misconfigured.
You can try to debug the error by setting error_score='raise'.

Below are more details about the failures:
--------------------------------------------------------------------------------
1 fits failed with the following error:
joblib.externals.loky.process_executor._RemoteTraceback: 
"""
Traceback (most recent call last):
  File "/Users/mjlk/Documents/GitHub/financial-fraud-detection/ml_pipeline/venv/lib/python3.11/site-packages/joblib/externals/loky/process_executor.py", line 490, in _process_worker
    r = call_item()
        ^^^^^^^^^^^
  File "/Users/mjlk/Documents/GitHub/financial-fraud-detection/ml_pipeline/venv/lib/python3.11/site-packages/joblib/externals/loky/process_executor.py", line 291, in __call__
    return self.fn(*self.args, **self.kwargs)
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/Users/mjlk/Documents/GitHub/financial-fraud-detection/ml_pipeline/venv/lib/python3.11/si

552:	learn: 0.0553080	total: 45s	remaining: 36.4s
372:	learn: 0.0683377	total: 42s	remaining: 1m 10s
147:	learn: 0.1149433	total: 9.61s	remaining: 55.3s
320:	learn: 0.0364058	total: 25.3s	remaining: 53.6s
506:	learn: 0.0522771	total: 42.2s	remaining: 41s
929:	learn: 0.0087857	total: 4m 50s	remaining: 21.8s
499:	learn: 0.0630727	total: 40.5s	remaining: 40.5s
190:	learn: 0.0277626	total: 43.3s	remaining: 3m 3s
555:	learn: 0.0509627	total: 45s	remaining: 35.9s
297:	learn: 0.0898422	total: 25.3s	remaining: 59.6s
102:	learn: 0.0991894	total: 6.71s	remaining: 58.4s
298:	learn: 0.0896340	total: 25.3s	remaining: 59.3s
513:	learn: 0.0534013	total: 40.5s	remaining: 38.3s
146:	learn: 0.0724490	total: 9.73s	remaining: 56.5s
100:	learn: 0.1482143	total: 6.73s	remaining: 59.9s
195:	learn: 0.0262395	total: 42.7s	remaining: 2m 55s
510:	learn: 0.0499287	total: 41.9s	remaining: 40.1s
556:	learn: 0.0509013	total: 45.1s	remaining: 35.8s
557:	learn: 0.0508494	total: 45.1s	remaining: 35.7s
501:	learn: 0.060

505:	learn: 0.0604460	total: 41.7s	remaining: 40.7s
372:	learn: 0.0575832	total: 43.6s	remaining: 1m 13s
376:	learn: 0.0679504	total: 42.5s	remaining: 1m 10s
415:	learn: 0.0567388	total: 46.4s	remaining: 1m 5s
324:	learn: 0.0357912	total: 25.9s	remaining: 53.8s
104:	learn: 0.1443770	total: 7.25s	remaining: 1m 1s
510:	learn: 0.0519164	total: 42.8s	remaining: 40.9s
416:	learn: 0.0566806	total: 46.4s	remaining: 1m 4s
325:	learn: 0.0355761	total: 25.9s	remaining: 53.6s
511:	learn: 0.0518554	total: 42.8s	remaining: 40.8s
108:	learn: 0.0934429	total: 7.25s	remaining: 59.3s
105:	learn: 0.1437797	total: 7.26s	remaining: 1m 1s
151:	learn: 0.0703263	total: 10.3s	remaining: 57.3s
520:	learn: 0.0528255	total: 41s	remaining: 37.7s
197:	learn: 0.0261156	total: 43.3s	remaining: 2m 55s
106:	learn: 0.1432695	total: 7.26s	remaining: 1m
109:	learn: 0.0922650	total: 7.25s	remaining: 58.7s
521:	learn: 0.0528064	total: 41s	remaining: 37.6s
506:	learn: 0.0603845	total: 41.7s	remaining: 40.6s
373:	learn: 0.05

In [ ]:
utils_assessment.get_summary_performances(logreg_performance_hybrid, parameter_column_name="Parameters summary")